In [1]:
# %pip install nest_asyncio

import asyncio

import nest_asyncio


nest_asyncio.apply()

In [2]:
# from airflow.decorators import task
import requests
import json
import os
import asyncio
from aiohttp import ClientSession

import pandas as pd
import numpy as np
import itertools
from datetime import datetime
from typing import Tuple
loop = asyncio.ProactorEventLoop()
asyncio.set_event_loop(loop)

In [3]:
MAXIMUM_CONCURRENT_REQUESTS = 150

riot_tokens = [
    "RGAPI-67ed0d57-028a-45d6-8d34-48e9e2e11d12", #PBE
    "RGAPI-196230a1-fdf0-4205-914f-3f269867e743", #NA
    "RGAPI-0899679e-51cd-4808-b5ba-2b739143e38f", #EUW
    "RGAPI-45a6e8c2-d736-4921-a246-05242bcc2b48", #EUNE
    "RGAPI-cd199ce7-9b4f-4ea7-9461-2f9015d8943c", #MAIN
]
region_groupings = {
    "br1":"americas",
    "eun1":"europe",
    "euw1":"europe",
    "jp1":"asia",
    "kr":"asia",
    "la1":"americas",
    "la2":"americas",
    "na1":"americas",
    "oc1":"sea",
    "tr1":"europe",
    "ru":"europe",
    "ph2":"sea",
    "sg2":"sea",
    "th2":"sea",
    "tw2":"sea",
    "vn2":"sea",
}

In [4]:
# start_date = datetime.now()
count = 0
rateLimitedCount = 0
async def getApiRequest(url, riot_token: str, fromRateLimited = 0) -> dict:
    header = {
        "Accept-Language": "en-US,en;q=0.9",
        "Accept-Charset": "application/x-www-form-urlencoded; charset=UTF-8",
        "Origin": "https://developer.riotgames.com",
        "X-Riot-Token": riot_token,
    }
    async with ClientSession() as session:
        async with session.get(url, headers=header) as response:
            global rateLimitedCount
            global count 
            count+=1
            if fromRateLimited :
                rateLimitedCount -=1
                print(f"No longer Rate limited count: {rateLimitedCount}")

            print(f"Took {datetime.now() - start_date} to complete {count} requests on {url} and API token {riot_token}")
            if response.status == 429:
                retry_after = int(response.headers.get('Retry-After', '1'))
                print("Rate limited, retrying after " + str(retry_after) + " seconds.")

                rateLimitedCount +=1
                print("Rate limited count: " + str(rateLimitedCount))

                await asyncio.sleep(retry_after)
                return await getApiRequest(url, riot_token,1)
            if response.status != 200:
                print(f"Error {response.status} on {url} with API {riot_token}")
            # assert response.status == 200
            return await response.json()
            

In [14]:
# @task(task_id="multiple_matches_ingest")
async def getMatchesRequestFromApi(matches: list[str]) -> list[dict]:
    requests_list = []
    for match in matches:
        print("Fetching match: " + match)
        region = region_groupings[match.split('_')[0].lower()]
        match_uri = f"https://{region}.api.riotgames.com/lol/match/v5/matches/{match}"
        requests_list.append(getApiRequest(match_uri, np.random.choice(riot_tokens,1)[0]))

    semaphore = asyncio.Semaphore(MAXIMUM_CONCURRENT_REQUESTS)
    async def semaphored_request(request):
        async with semaphore:
            return await request
    return await asyncio.gather(*(semaphored_request(request) for request in requests_list))

async def getMultiplePlayerMatchesFromApi(player_uuids : list[tuple], match_count : int ) -> list[dict]:
    requests_list = []
    for puuid, region_group, riot_token in player_uuids:
        request = getApiRequest(f"https://{region_group}.api.riotgames.com/lol/match/v5/matches/by-puuid/{puuid}/ids?start=0&count={match_count}", riot_token)
        requests_list.append(request)

    semaphore = asyncio.Semaphore(MAXIMUM_CONCURRENT_REQUESTS)
    async def semaphored_request(request):
        async with semaphore:
            return await request
        
    return await asyncio.gather(*(semaphored_request(request) for request in requests_list))
    # return await asyncio.gather(*requests_list)
    
async def getLeagueEntriesFromApi(queue: str, tier :str, division:str, page:int , region : str, riot_token : str) -> list[dict]:
    request = getApiRequest(f"https://{region}.api.riotgames.com/lol/league-exp/v4/entries/{queue}/{tier}/{division}?page={page}", riot_token)
    return await asyncio.gather(*[request])

async def getTopLeagueEntriesFromApi(queue : str, tier:str, region : str, riot_token : str) -> list[dict]:
    request = getApiRequest(f"https://{region}.api.riotgames.com/lol/league/v4/{tier}/by-queue/{queue}", riot_token)
    return await asyncio.gather(*[request])

async def getMultiplePlayerEntriesFromApi(players : list[tuple]): #By SummonnerID -> "id" in JSON file
    requests_list = []

    for region, summonerID, riot_token in players:
        requests_list.append(getApiRequest(f"https://{region}.api.riotgames.com/lol/summoner/v4/summoners/{summonerID}", str(riot_token)))
    
    semaphore = asyncio.Semaphore(MAXIMUM_CONCURRENT_REQUESTS)
    async def semaphored_request(request):
        async with semaphore:
            return await request
    
    # return await asyncio.gather(*requests_list)
    return await asyncio.gather(*(semaphored_request(request) for request in requests_list))

async def getMultiplePlayerMasterIdsFromApi(summoner_ids : list[tuple]):
    requests_list = []
    for encryptedSummonerId, region, riot_token in summoner_ids:
        request = getApiRequest(f"https://{region}.api.riotgames.com/lol/champion-mastery/v4/champion-masteries/by-summoner/{encryptedSummonerId}", riot_token)
        requests_list.append(request)

    semaphore = asyncio.Semaphore(MAXIMUM_CONCURRENT_REQUESTS)
    async def semaphored_request(request):
        async with semaphore:
            return await request
        
    return await asyncio.gather(*(semaphored_request(request) for request in requests_list))

In [16]:
# @task(task_id="multiple_matches_ingest")
def ingestMultipleMatches(matches: list[str], limit = None) -> list[dict]:
    if limit is None:
        limit = len(matches)
    
    return asyncio.run(getMatchesRequestFromApi(itertools.islice(matches, 0, limit-1)))

# @task(task_id="ingestMultiplePlayerMatches")
def ingestMultiplePlayerMatches(player_uuids : list[tuple], match_count : int = 20) -> list[dict]:
    return asyncio.run(getMultiplePlayerMatchesFromApi(player_uuids, match_count))
    
# @task(task_id="ingestLeagueEntries")
def ingestLeagueEntries(queue: str, tier :str, division:str, region, riot_token : str, page:int = 1) -> list[dict]:
    return asyncio.run(getLeagueEntriesFromApi(queue, tier, division, page, region, riot_token))[0]

# @task(task_id="ingestTopLeagueEntries")
def ingestTopLeagueEntries(queue: str, tier:str,region, riot_token : str) -> dict:
    return asyncio.run(getTopLeagueEntriesFromApi(queue, tier, region,riot_token))[0]

# @task(task_id="player_ingest")
def ingestMultiplePlayerEntries(players : list[tuple]) -> list[dict]:
    return asyncio.run(getMultiplePlayerEntriesFromApi(players))

def ingestMultiplePlayerMasterIds(summoner_ids : list[tuple]) -> list[dict]:
    return asyncio.run(getMultiplePlayerMasterIdsFromApi(summoner_ids))

### Clean DataFrame

In [7]:
# @task(task_id="parseDataFrameDtypes")
def parseDataFrameDtypes(df: pd.DataFrame, categorical_columns = [], int_columns = [], datetime_columns = []) -> pd.DataFrame:
    for column in categorical_columns:
        df[column] = df[column].astype("category")
    for column in int_columns:
        df[column] = df[column].astype("int")
    for column in datetime_columns:
        df[column] = pd.to_datetime(df[column])
    return df

# @task(task_id="reorder_coluns")
def reorderColumns(df: pd.DataFrame, ordered_columns: list[str]) -> pd.DataFrame:
    return df.reindex(columns=ordered_columns)

# @task(task_id="cleanDataframe")
def cleanDataframe(df: pd.DataFrame, categorical_columns = [], int_columns = [], datetime_columns = [], ordered_columns = []) -> pd.DataFrame:
    df = parseDataFrameDtypes(df, categorical_columns, int_columns, datetime_columns)
    if len(ordered_columns) > 0:
        df = reorderColumns(df, ordered_columns)
    return df

### Saving output to csv

In [8]:
# @task(task_id="save_to_csv")
def save_to_csv(df: pd.DataFrame, path: str, index: bool = False) -> None:
    """
        Note: Saving to CSV files are only temporary and will be removed after the entire piepline is completed.
    """
    if(os.path.exists(path)):
        df.to_csv(path, index=index, mode='a', header=False)
    else:
        df.to_csv(path, index=index, mode='w', header=True)

### League Entries

In [9]:
#League Infos and Player League Infos is separated

# @task(task_id="getTopLeagueEntries")
def getTopLeagueEntries(queue: str, tier :str, region) -> Tuple[pd.DataFrame, pd.DataFrame]:
    riot_token : str = np.random.choice(riot_tokens)
    league_entries_raw : dict = ingestTopLeagueEntries(queue, tier, region, riot_token)

    if not league_entries_raw:
        return pd.DataFrame(), pd.DataFrame()
    
    current_time = datetime.now()

    player_league_infos = pd.DataFrame(league_entries_raw["entries"])
    player_league_infos["leagueId"] = league_entries_raw.get("leagueId")
    player_league_infos["last_updated"] = datetime.now()
    player_league_infos["riot_token"] = riot_token
    player_league_infos["region"] = region
    # player_league_infos = reorderColumns(player_league_infos, ordered_columns= ["leagueId","region","summonerId","summonerName","leaguePoints","rank","wins","losses","veteran","inactive","freshBlood","hotStreak","last_updated","riot_token"])

    del league_entries_raw["entries"]
    league_infos = pd.DataFrame([league_entries_raw])
    league_infos["last_updated"] = datetime.now()
    league_infos["queue"] = queue
    league_infos["region"] = region
    league_infos["division"] = 'I'
    league_infos["riot_token"] = riot_token
    # league_infos = reorderColumns(league_infos, ordered_columns= ["leagueId","region","queue","tier","division","name","last_updated","riot_token"])
    return league_infos, player_league_infos

# @task(task_id="getLeagueEntries")
def getNormalLeagueEntries(queue: str, tier :str, division:str, region : str, pages : int) -> Tuple[pd.DataFrame, pd.DataFrame]:
    player_leauge_infos_list = []
    league_infos_list = []
    for page in range(1, pages+1):
        riot_token : str = np.random.choice(riot_tokens)
     
        league_entries_raw : dict = pd.DataFrame.from_dict(ingestLeagueEntries(queue, tier, division, region, riot_token, page))

        if league_entries_raw.empty:
            return pd.DataFrame(), pd.DataFrame()

        player_league_infos = league_entries_raw.loc[:,['leagueId','summonerId','summonerName','leaguePoints','rank','wins','losses','veteran','inactive','freshBlood','hotStreak']]
        player_league_infos["last_updated"] = datetime.now()
        player_league_infos["riot_token"] = riot_token
        player_league_infos["region"] = region
        player_leauge_infos_list.append(player_league_infos)
        # player_league_infos = reorderColumns(player_league_infos,["leagueId","region","summonerId","summonerName","leaguePoints","rank","wins","losses","veteran","inactive","freshBlood","hotStreak","last_updated","riot_token"])

        league_infos = league_entries_raw.loc[:,['leagueId','tier']]
        league_infos["region"] = region
        league_infos["queue"] = queue
        league_infos["division"] = league_entries_raw["rank"]
        league_infos["last_updated"] = datetime.now()
        league_infos["riot_token"] = riot_token
        # league_infos = reorderColumns(league_infos, ordered_columns= ["leagueId","region","queue","tier","division","name","last_updated","riot_token"])
        league_infos.drop_duplicates(subset=["leagueId"], inplace=True)
        league_infos_list.append(league_infos)

    return pd.concat(league_infos_list, axis=0), pd.concat(player_leauge_infos_list,axis=0)

# @task(task_id="all_league_entries")
def getLeagueEntries(queue : str,
                   tier : str, 
                   division: str = None,
                   regions: list[str] = ["ph2", "eun1", "euw1", "jp1", "kr", "la1", "la2", "na1", "oc1", "ru", "sg2", "th2", "tr1", "tw2", "vn2","br1"],
                   pages : int = 1):
    """
        Main function for ingestion of data for leagues.
        Args:
            queue::str:
                The queue type of the league.  All valid values accepted according to API: RANK_FLEX_SR, RANK_FLEX_TT, RANKED_SOLO_5x5. Note that RANK_FLEX_TT is deprecated.
            tier::str:
                The league tier.  The following values are accepted: challengerleagues, grandmasterleagues, masterleagues, DIAMOND, PLATINUM, GOLD, SILVER, BRONZE, IRON
            division::str:
                The league division.  All valid values accepted according to API: I, II, III, IV.  Challenger to Master divisions only have one division.
            region::str:
                The region of the league. Default: All regions.  All valid values accepted according to API: ph2, eun1, euw1, jp1, kr, la1, la2, na1, oc1, ru, sg2, th2, tr1, tw2, vn2
            pages::int:
                The number of pages to be ingested.  Each page contains >20 entries and varies per region. Challenger to Master divisions always show the complete list (only 1 page).  
        Returns:
            None
    """
    league_infos_list = []
    if tier in ["challengerleagues", "grandmasterleagues", "masterleagues"]:
        league_infos_list = [getTopLeagueEntries(queue=queue, tier=tier, region=region) for region in regions]
    else:
        if division is None:
            raise ValueError("Division must be specified for non-Challenger to Master divisions.")
        league_infos_list = [getNormalLeagueEntries(queue=queue, tier=tier, division=division, region=region, pages=pages) for region in regions]

    league_infos_list = list(zip(*league_infos_list))
    return pd.concat(league_infos_list[0],axis=0), pd.concat(league_infos_list[1],axis=0)


### Player Details

In [10]:
league_info, player_league_info = getLeagueEntries(queue="RANKED_SOLO_5x5", tier="challengerleagues", division='I', pages=1)
player_ids = list(player_league_info[["region","summonerId","riot_token"]].itertuples(index=False, name=None))
player_info = ingestMultiplePlayerEntries(player_ids)

Took 0:00:02.034533 to complete 1 requests on https://ph2.api.riotgames.com/lol/league/v4/challengerleagues/by-queue/RANKED_SOLO_5x5 and API token RGAPI-45a6e8c2-d736-4921-a246-05242bcc2b48
Took 0:00:03.347529 to complete 2 requests on https://eun1.api.riotgames.com/lol/league/v4/challengerleagues/by-queue/RANKED_SOLO_5x5 and API token RGAPI-cd199ce7-9b4f-4ea7-9461-2f9015d8943c
Took 0:00:04.774530 to complete 3 requests on https://euw1.api.riotgames.com/lol/league/v4/challengerleagues/by-queue/RANKED_SOLO_5x5 and API token RGAPI-cd199ce7-9b4f-4ea7-9461-2f9015d8943c
Took 0:00:05.279094 to complete 4 requests on https://jp1.api.riotgames.com/lol/league/v4/challengerleagues/by-queue/RANKED_SOLO_5x5 and API token RGAPI-0899679e-51cd-4808-b5ba-2b739143e38f
Took 0:00:06.032699 to complete 5 requests on https://kr.api.riotgames.com/lol/league/v4/challengerleagues/by-queue/RANKED_SOLO_5x5 and API token RGAPI-67ed0d57-028a-45d6-8d34-48e9e2e11d12
Took 0:00:07.062890 to complete 6 requests on htt

In [11]:
accounts_raw = pd.DataFrame(player_info).merge(player_league_info, left_on='id', right_on = 'summonerId', how='left')

accounts_raw["region_group"] = accounts_raw["region"].map(region_groupings)
assert accounts_raw["region_group"].isna().sum() == 0

# display(accounts_raw["region"].unique())
match_history_raw = ingestMultiplePlayerMatches(list(accounts_raw[['puuid','region_group','riot_token']].itertuples(index=False, name=None)))

Took 0:16:47.726826 to complete 7123 requests on https://sea.api.riotgames.com/lol/match/v5/matches/by-puuid/hWTZCy_0JUTmLwKqdsVrUAWO3E9dLni3aTVEFn8vmmKWbEagGqb0Jryq7AP2_xNwe5k08AAhHXjgdQ/ids?start=0&count=20 and API token RGAPI-45a6e8c2-d736-4921-a246-05242bcc2b48
Rate limited, retrying after 2 seconds.
Rate limited count: 1
Took 0:16:47.736813 to complete 7124 requests on https://sea.api.riotgames.com/lol/match/v5/matches/by-puuid/v1HdGeSOC85ypRE97ZAEdYyKM3UUnHFfz0B96U2OJmYSmPCGGiWNDqFl93ulJCYONIaIMyYHxGVpEQ/ids?start=0&count=20 and API token RGAPI-45a6e8c2-d736-4921-a246-05242bcc2b48
Rate limited, retrying after 2 seconds.
Rate limited count: 2
Took 0:16:47.737969 to complete 7125 requests on https://sea.api.riotgames.com/lol/match/v5/matches/by-puuid/ppmGf4QR0Ou4NSRiR0nLgFoEQU0ZN-lTEgQq73W184HJD4ZzXfBRzXcmw46qPehgFd8eAO8mYw8Z3Q/ids?start=0&count=20 and API token RGAPI-45a6e8c2-d736-4921-a246-05242bcc2b48
Rate limited, retrying after 2 seconds.
Rate limited count: 3
Took 0:16:47.737

In [28]:
match_history_list = set(itertools.chain.from_iterable(match_history_raw))
raw_match_history_details = ingestMultipleMatches(match_history_list, 200)

Fetching match: TW2_49414692
Fetching match: EUW1_6327779073
Fetching match: LA1_1369394442
Fetching match: LA2_1281162879
Fetching match: VN2_55075528
Fetching match: VN2_55263971
Fetching match: BR1_2695952257
Fetching match: JP1_391187439
Fetching match: TR1_1392007896
Fetching match: BR1_2693024280
Fetching match: NA1_4610339524
Fetching match: JP1_390651779
Fetching match: RU_434348167
Fetching match: OC1_563840347
Fetching match: LA2_1279397187
Fetching match: RU_434820713
Fetching match: EUW1_6324166862
Fetching match: LA1_1369215229
Fetching match: VN2_55255559
Fetching match: VN2_54941866
Fetching match: NA1_4609943736
Fetching match: EUW1_6331899281
Fetching match: LA2_1279643352
Fetching match: EUN1_3338023671
Fetching match: TR1_1390940449
Fetching match: EUW1_6323998967
Fetching match: BR1_2700849113
Fetching match: EUW1_6325169860
Fetching match: LA1_1369649055
Fetching match: VN2_50044524
Fetching match: EUW1_6329450752
Fetching match: EUW1_6328923753
Fetching match: PH2

### Match Details   

In [84]:
# @task(task_id="match_general_info")
def getMatchGeneralInfo(raw_match: dict) -> dict:
    match = {}

    match['matchId'] = raw_match['metadata']['matchId']
    match['last_update'] = datetime.now()
    keys_to_exlude = {
        "participants",
        "teams",
    }
    match |= { key:raw_match["metadata"][key] for key in set(set(raw_match["metadata"].keys()) - keys_to_exlude)}
    match |= { key:raw_match["info"][key] for key in set(set(raw_match["info"].keys()) - keys_to_exlude)}
    return match

# @task(task_id = "match_players_info")
def getMatchPlayersInfo(raw_match: dict) -> list[dict]:
    if raw_match is None:
        print("Match none detected")
        return {}
    
    keys_initial_exclude = {
        "challenges",
        "perks",
    }

    raw_participants_details  : list[dict] = raw_match["info"]["participants"]

    final_participants_details : list[dict] = []
    
    for raw_participant in raw_participants_details:
        participant = {}
        participant["matchId"] = raw_match["metadata"]["matchId"]
        participant['last_update'] = datetime.now()

        #Normal Keys
        participant |= { key:raw_participant[key] for key in set(set(raw_participant.keys()) - keys_initial_exclude)}

        #Challenges DTO flattened
        if "challenges" in raw_participant.keys():
            participant |= { f"challenges_{key}":raw_participant["challenges"][key] for key in raw_participant["challenges"].keys()}

        #Runes DTO stat perks flattened
        participant |= { f"statPerks_{key}": raw_participant["perks"]["statPerks"][key] for key in raw_participant["perks"]["statPerks"].keys() }
        
        #Runes DTO styles flattened
        for style in raw_participant["perks"]["styles"]:
            temp = {}

            style_type = style['description']
            temp[f"{ style_type }_id"] = style["style"]
            
            #PerkStyleSelectionDto
            for index, perk in enumerate(style["selections"]):
                temp[f"{style_type}_{index}_id"] = perk["perk"]
                temp[f"{style_type}_{index}_var1"] = perk["var1"]
                temp[f"{style_type}_{index}_var2"] = perk["var2"]
                temp[f"{style_type}_{index}_var3"] = perk["var3"]
            
            participant |= temp

        final_participants_details.append(participant)
    
    return final_participants_details

def getMatchTeamsInfo(raw_match: dict) -> dict:
    teams_info_raw = raw_match["info"]["teams"]
    teams_info = {}

    teams_info["matchId"] = raw_match["metadata"]["matchId"]
    teams_info['last_update'] = datetime.now()
    for team in teams_info_raw:
        team_name = "blue" if team["teamId"] == 100 else "red"
        for bans in team["bans"]:
            teams_info[f"bans_turn_{bans['pickTurn']}"] = bans["championId"]
        for objective in team["objectives"].keys():
            teams_info[f"{team_name}_{objective}_isFirstKill"] = team["objectives"][objective]["first"]
            teams_info[f"{team_name}_{objective}_kills"] = team["objectives"][objective]["kills"]
        teams_info[f"{team_name}_win"] = team["win"]
    
    

    return teams_info

def getMultipleMatchInfo(raw_matches: list[dict]) -> Tuple[pd.DataFrame, pd.DataFrame, pd.DataFrame]:
    match_general_info = []
    match_players_info = []
    match_teams_info = []

    for match in raw_matches:
        match_general_info.append(getMatchGeneralInfo(match))
        match_players_info.append(getMatchPlayersInfo(match))
        match_teams_info.append(getMatchTeamsInfo(match))

    match_general_info = pd.DataFrame(match_general_info)
    match_players_info = pd.DataFrame(itertools.chain.from_iterable(match_players_info))
    match_teams_info = pd.DataFrame(match_teams_info)
    
    return match_general_info, match_players_info, match_teams_info




In [85]:
match_general_info, match_players_info, match_teams_info = getMultipleMatchInfo(raw_match_history_details)

display(match_general_info.head())

display(match_players_info.head())
display(match_teams_info.head())

matchId                last_update dataVersion  gameDuration  \
0     TW2_49414692 2023-03-26 14:28:41.878614           2          1555   
1  EUW1_6327779073 2023-03-26 14:28:41.879616           2          1045   
2   LA1_1369394442 2023-03-26 14:28:41.880622           2          1138   
3   LA2_1281162879 2023-03-26 14:28:41.881616           2           918   
4     VN2_55075528 2023-03-26 14:28:41.882615           2           931   

   gameEndTimestamp  mapId  gameStartTimestamp gameMode    gameVersion  \
0     1679723116720     11       1679721561618  CLASSIC  13.6.499.7758   
1     1679582179217     11       1679581133967  CLASSIC   13.6.499.913   
2     1679533147555     12       1679532008938     ARAM   13.6.499.913   
3     1679710316932     11       1679709398709  CLASSIC  13.6.499.7758   
4     1679752433574     11       1679751502275  CLASSIC  13.6.499.7758   

   queueId   gameCreation      gameId      gameType tournamentCode  \
0      430  1679721502064    49414692  MATCHED_GAME                  
1      420  1679581073315  6327779073  MATCHED_GAME                  
2      450  1679531909218  1369394442  MATCHED_GAME                  
3      420  1679709332228  1281162879  MATCHED_GAME                  
4      430  1679751288233    55075528  MATCHED_GAME                  

                       gameName platformId  
0    teambuilder-match-49414692        TW2  
1  teambuilder-match-6327779073       EUW1  
2  teambuilder-match-1369394442        LA1  
3  teambuilder-match-1281162879        LA2  
4    teambuilder-match-55075528        VN2

matchId                last_update riotIdName summonerName  \
0  TW2_49414692 2023-03-26 14:28:41.878614               GRAND KIA   
1  TW2_49414692 2023-03-26 14:28:41.878614                     ÖKœ   
2  TW2_49414692 2023-03-26 14:28:41.878614                    煞蜜拉K   
3  TW2_49414692 2023-03-26 14:28:41.878614                早餐吃豬排蛋吐司   
4  TW2_49414692 2023-03-26 14:28:41.878614                    嘿嘿嘿x   

   totalUnitsHealed  item2  spell1Casts  largestCriticalStrike  timePlayed  \
0                 1   2055           92                    505        1555   
1                 5   2065           43                      0        1555   
2                 1   3006          705                    383        1555   
3                 1   6657           79                    172        1555   
4                 1   3158          122                      0        1555   

   totalHeal  ...  challenges_fasterSupportQuestCompletion  \
0       9957  ...                                      NaN   
1       7926  ...                                      NaN   
2       6208  ...                                      NaN   
3       2293  ...                                      NaN   
4       2850  ...                                      NaN   

   challenges_soloTurretsLategame  challenges_playedChampSelectPosition  \
0                             NaN                                   NaN   
1                             NaN                                   NaN   
2                             NaN                                   NaN   
3                             NaN                                   NaN   
4                             NaN                                   NaN   

   challenges_shortestTimeToAceFromFirstTakedown  challenges_fastestLegendary  \
0                                            NaN                          NaN   
1                                            NaN                          NaN   
2                                            NaN                          NaN   
3                                            NaN                          NaN   
4                                            NaN                          NaN   

   challenges_hadAfkTeammate  challenges_teleportTakedowns  \
0                        NaN                           NaN   
1                        NaN                           NaN   
2                        NaN                           NaN   
3                        NaN                           NaN   
4                        NaN                           NaN   

   challenges_earliestElderDragon  challenges_thirdInhibitorDestroyedTime  \
0                             NaN                                     NaN   
1                             NaN                                     NaN   
2                             NaN                                     NaN   
3                             NaN                                     NaN   
4                             NaN                                     NaN   

   challenges_mejaisFullStackInTime  
0                               NaN  
1                               NaN  
2                               NaN  
3                               NaN  
4                               NaN  

[5 rows x 278 columns]

matchId                last_update  blue_baron_isFirstKill  \
0     TW2_49414692 2023-03-26 14:28:41.879616                    True   
1  EUW1_6327779073 2023-03-26 14:28:41.880622                   False   
2   LA1_1369394442 2023-03-26 14:28:41.881616                   False   
3   LA2_1281162879 2023-03-26 14:28:41.882615                   False   
4     VN2_55075528 2023-03-26 14:28:41.883634                   False   

   blue_baron_kills  blue_champion_isFirstKill  blue_champion_kills  \
0                 1                       True                   23   
1                 0                       True                   22   
2                 0                       True                   66   
3                 0                      False                    9   
4                 0                       True                   19   

   blue_dragon_isFirstKill  blue_dragon_kills  blue_inhibitor_isFirstKill  \
0                    False                  1                        True   
1                     True                  1                        True   
2                    False                  0                        True   
3                    False                  0                       False   
4                     True                  1                        True   

   blue_inhibitor_kills  ...  bans_turn_1  bans_turn_2  bans_turn_3  \
0                     1  ...          NaN          NaN          NaN   
1                     2  ...        107.0         67.0         22.0   
2                     1  ...          NaN          NaN          NaN   
3                     0  ...        107.0         81.0         76.0   
4                     2  ...          NaN          NaN          NaN   

   bans_turn_4  bans_turn_5  bans_turn_6  bans_turn_7  bans_turn_8  \
0          NaN          NaN          NaN          NaN          NaN   
1         29.0         85.0        902.0         64.0         54.0   
2          NaN          NaN          NaN          NaN          NaN   
3         79.0         24.0        120.0        122.0        112.0   
4          NaN          NaN          NaN          NaN          NaN   

   bans_turn_9  bans_turn_10  
0          NaN           NaN  
1          7.0         119.0  
2          NaN           NaN  
3         53.0         350.0  
4          NaN           NaN  

[5 rows x 38 columns]

In [87]:
display(accounts_raw.head())

id  \
0  kB8pnzOR_Go0IL1ZNvZipC2FokPGkU_Nmd_lhG3BfmJx_-...   
1  elwUen1ydLSZBXnbOqrg20MgVm-gg1ZUHSQCejB3tA0EGD...   
2  o-Bvzq1AElfFhBsPJCmXJFkgW5Oux_jPN2xYWL6vkQrpw5...   
3  uPQsb7QJW_zLiumvwYgZIRSH1x8Gt3Uq44NZOAWruTHcyL...   
4  raQ1he7m0u9OiqMNYUUgBL2xr8P-9atnZo1WK-pEOxsHyM...   

                                           accountId  \
0  Pm3a46QsuaWCxZvIzrvUZf_Ob5cpCyXLYugrQNK04gL7Ew...   
1  iD2nB9OYcr1uQDflnWIlObDdLv7aIgrnIUa6Ol1CWoQZ0E...   
2  G9_mEQgDWC5EWHROjw_EA9fdtZFSSuNEWErguXnNfZNN7D...   
3  HAbH19RDEc5PgNLCKotnxt9u8UkMZTysdRwwxgCZhPlyYg...   
4  LHIE_0u3bLDXa8ei-54NbZZb7Xm-BnNOuXVGJMSL6B_jRB...   

                                               puuid       name  \
0  tLYl_PJNM2WzuIVHqKU0l2fkmribeZYuzEHmgtIURDLPga...   Nightvol   
1  wRQbX-MJAVUFePf-RFrKFomEKjhv_fdjUr-j0yXS3VYHIA...   Gwangdae   
2  qCO-ny_v460jGosP3OJod1q8Uthm7ObWaq94sYL2K8T5z9...  do better   
3  KPQRKnD--iznAL9L3u9IAK6aMw_AIgZbXtKh5kRAg-_lLS...   我的爱你在哪里啊   
4  dm80a235o_pRgGUaHR_3xtldj2wPvLsWis__iqini4kzEa...     motShi   

   profileIconId   revisionDate  summonerLevel  \
0           3592  1679754805631            477   
1           5449  1679749968148            461   
2             29  1679606056000            141   
3           5448  1679797572339            742   
4           4833  1679757290847            515   

                                          summonerId summonerName  \
0  kB8pnzOR_Go0IL1ZNvZipC2FokPGkU_Nmd_lhG3BfmJx_-...     Nightvol   
1  elwUen1ydLSZBXnbOqrg20MgVm-gg1ZUHSQCejB3tA0EGD...     Gwangdae   
2  o-Bvzq1AElfFhBsPJCmXJFkgW5Oux_jPN2xYWL6vkQrpw5...    do better   
3  uPQsb7QJW_zLiumvwYgZIRSH1x8Gt3Uq44NZOAWruTHcyL...     我的爱你在哪里啊   
4  raQ1he7m0u9OiqMNYUUgBL2xr8P-9atnZo1WK-pEOxsHyM...       motShi   

   leaguePoints  ... losses  veteran  inactive  freshBlood  hotStreak  \
0           623  ...     56    False     False       False      False   
1           761  ...     62    False     False       False      False   
2           563  ...    117    False     False       False      False   
3           515  ...    107    False     False        True       True   
4          1109  ...     44    False     False       False       True   

                               leagueId               last_updated  \
0  1f86eec6-f8b3-38ec-b06e-f19640b284e1 2023-03-26 13:04:10.415433   
1  1f86eec6-f8b3-38ec-b06e-f19640b284e1 2023-03-26 13:04:10.415433   
2  1f86eec6-f8b3-38ec-b06e-f19640b284e1 2023-03-26 13:04:10.415433   
3  1f86eec6-f8b3-38ec-b06e-f19640b284e1 2023-03-26 13:04:10.415433   
4  1f86eec6-f8b3-38ec-b06e-f19640b284e1 2023-03-26 13:04:10.415433   

                                   riot_token region region_group  
0  RGAPI-45a6e8c2-d736-4921-a246-05242bcc2b48    ph2          sea  
1  RGAPI-45a6e8c2-d736-4921-a246-05242bcc2b48    ph2          sea  
2  RGAPI-45a6e8c2-d736-4921-a246-05242bcc2b48    ph2          sea  
3  RGAPI-45a6e8c2-d736-4921-a246-05242bcc2b48    ph2          sea  
4  RGAPI-45a6e8c2-d736-4921-a246-05242bcc2b48    ph2          sea  

[5 rows x 22 columns]

In [ ]:
accounts_list = list(accounts_raw[['id','region','riot_token']].itertuples(index=False, name=None))
player_champion_mastery_info = itertools.chain.from_iterable(ingestMultiplePlayerMasterIds(accounts_list))



In [89]:
player_champion_mastery_info = pd.DataFrame(player_champion_mastery_info).merge(accounts_raw[['summonerId','summonerName','region']], on='summonerId', how='left')
pd.DataFrame(player_champion_mastery_info)

championId  championLevel  championPoints   lastPlayTime  \
0               99              7          266305  1678629975000   
1               81              7          189620  1677933537000   
2              101              5          187015  1679748544000   
3                7              5          137542  1678624847000   
4              163              5          136797  1677738573000   
...            ...            ...             ...            ...   
345567          62              1             137  1652489042000   
345568         246              1             136  1572627307000   
345569          82              1             115  1613447414000   
345570         234              1             109  1623767885000   
345571         133              1             107  1615133985000   

        championPointsSinceLastLevel  championPointsUntilNextLevel  \
0                             244705                             0   
1                             168020                             0   
2                             165415                             0   
3                             115942                             0   
4                             115197                             0   
...                              ...                           ...   
345567                           137                          1663   
345568                           136                          1664   
345569                           115                          1685   
345570                           109                          1691   
345571                           107                          1693   

        chestGranted  tokensEarned  \
0              False             0   
1              False             0   
2               True             2   
3              False             2   
4               True             2   
...              ...           ...   
345567         False             0   
345568         False             0   
345569         False             0   
345570         False             0   
345571         False             0   

                                               summonerId summonerName region  
0       kB8pnzOR_Go0IL1ZNvZipC2FokPGkU_Nmd_lhG3BfmJx_-...     Nightvol    ph2  
1       kB8pnzOR_Go0IL1ZNvZipC2FokPGkU_Nmd_lhG3BfmJx_-...     Nightvol    ph2  
2       kB8pnzOR_Go0IL1ZNvZipC2FokPGkU_Nmd_lhG3BfmJx_-...     Nightvol    ph2  
3       kB8pnzOR_Go0IL1ZNvZipC2FokPGkU_Nmd_lhG3BfmJx_-...     Nightvol    ph2  
4       kB8pnzOR_Go0IL1ZNvZipC2FokPGkU_Nmd_lhG3BfmJx_-...     Nightvol    ph2  
...                                                   ...          ...    ...  
345567     j_y0NYWC_Bi90KZHNKI92gsHYqoFOPYS3tbZl6atiJf1wQ    LOUD Ceos    br1  
345568     j_y0NYWC_Bi90KZHNKI92gsHYqoFOPYS3tbZl6atiJf1wQ    LOUD Ceos    br1  
345569     j_y0NYWC_Bi90KZHNKI92gsHYqoFOPYS3tbZl6atiJf1wQ    LOUD Ceos    br1  
345570     j_y0NYWC_Bi90KZHNKI92gsHYqoFOPYS3tbZl6atiJf1wQ    LOUD Ceos    br1  
345571     j_y0NYWC_Bi90KZHNKI92gsHYqoFOPYS3tbZl6atiJf1wQ    LOUD Ceos    br1  

[345572 rows x 11 columns]